[Jupyter Book](https://geo-smart.github.io/oceanography/intro.html) and [GitHub repo](https://github.com/geo-smart/oceanography).


# GLODAP: Global Ocean Data Analysis Project


This notebook is a viewer for global ocean chemistry. It depends upon downloading local copies
of five data files. The data are organized as depth-sorted layers of the global ocean (where the
depths are predetermined). The data files are not part of this Jupyter Book due to size limits.




The [GLODAP](https://en.wikipedia.org/wiki/Global_Ocean_Data_Analysis_Project) 
global ocean dataset compiles several decades of observation. It is a 'geological instant' snapshot of
the state of the entire ocean.


Moving the sliders for each chart selects for depth, as shown at the bottom left.



- GLODAP data used here is the 2016 version; 2021 v2 available
- Color map cmocean
- Make a subset intrinsic, show by default e.g. Atlantic / Caribbean / Amazon



This sequence of download commands gets five global ocean state datasets.

```
!mkdir glodap
!wget -q https://kilroybackup.s3.us-west-2.amazonaws.com/glodap/NO3.nc         -O glodap/NO3.nc
!wget -q https://kilroybackup.s3.us-west-2.amazonaws.com/glodap/TCO2.nc        -O glodap/TCO2.nc
!wget -q https://kilroybackup.s3.us-west-2.amazonaws.com/glodap/oxygen.nc      -O glodap/oxygen.nc
!wget -q https://kilroybackup.s3.us-west-2.amazonaws.com/glodap/salinity.nc    -O glodap/salinity.nc
!wget -q https://kilroybackup.s3.us-west-2.amazonaws.com/glodap/temperature.nc -O glodap/temperature.nc
```

#### Artifact: configuration


```
import os, sys, time, glob, warnings, cmocean
from IPython.display import clear_output
warnings.filterwarnings('ignore')
this_dir = os.getcwd()  

from matplotlib import animation, rc
from numpy import datetime64 as dt64, timedelta64 as td64
```

In [1]:
from matplotlib import pyplot as plt, colors as mplcolors
import numpy as np, pandas as pd, xarray as xr
from ipywidgets import *
from traitlets import dlink

In [3]:
glodapdir = '../../../data/oceanography/glodap/'         # this is a location outside of the repository

temperatureFnm = glodapdir + 'temperature.nc'
salinityFnm    = glodapdir + 'salinity.nc'
oxygenFnm      = glodapdir + 'oxygen.nc'
NO3Fnm         = glodapdir + 'NO3.nc'
TCO2Fnm        = glodapdir + 'TCO2.nc'

glodap = {}
glodap['S'] = xr.open_dataset(salinityFnm)
glodap['T'] = xr.open_dataset(temperatureFnm)
glodap['O'] = xr.open_dataset(oxygenFnm)
glodap['N'] = xr.open_dataset(NO3Fnm)
glodap['R'] = xr.open_dataset(TCO2Fnm)

In [6]:
for ds in glodap: print(ds)

# should print S T O N R respectively Salinity, Temperature, Oxygen, Nitrate, CO2

S
T
O
N
R


In [7]:
def oxygen(depth_index):
    glodap['O']['oxygen'].sel(depth_surface = depth_index).plot(figsize=(11, 7),cmap='viridis',vmin=150, vmax=350)         # original: cmocean.cm.oxy
    plt.ylabel(None); plt.xlabel(None)
    if depth_index == 0: msg = 'This is for surface water'
    else:                msg = 'This is for water at ' + str(int(glodap['O']['Depth'].values[depth_index])) + ' meters depth'
    plt.text(25, -87, msg); plt.text(28, 50, 'oxygen dissolved in'); plt.text(28, 42, '     ocean water   ')

interact(oxygen, depth_index=widgets.IntSlider(min=0, max=32, step=1, value=0, continuous_update=False, description='O depth'))

interactive(children=(IntSlider(value=0, continuous_update=False, description='O depth', max=32), Output()), _…

<function __main__.oxygen(depth_index)>

In [8]:
plt.rcParams.update({'font.size': 16})

# return to cmocean.cm.oxy, haline, thermal, algae, delta

def oxygen(depth_index):
    glodap['O']['oxygen'].sel(depth_surface = depth_index).plot(figsize=(11, 7),cmap='viridis', vmin=150, vmax=350)
    plt.ylabel(None); plt.xlabel(None)
    if depth_index == 0: msg = 'This is for surface water'
    else:                msg = 'This is for water at ' + str(int(glodap['O']['Depth'].values[depth_index])) + ' meters depth'
    plt.text(25, -87, msg); plt.text(28, 50, 'oxygen dissolved in'); plt.text(28, 42, '     ocean water   ')

def salinity(depth_index):
    glodap['S']['salinity'].sel(depth_surface = depth_index).plot(figsize=(11, 7),cmap='plasma',vmin=33, vmax=36)
    plt.ylabel(None); plt.xlabel(None)
    if depth_index == 0: msg = 'This is for surface water'
    else:                msg = 'This is for water at ' + str(int(glodap['S']['Depth'].values[depth_index])) + ' meters depth'
    plt.text(25, -87, msg); plt.text(47, 50, 'salinity of'); plt.text(47, 42, 'ocean water')

def temperature(depth_index):
    glodap['T']['temperature'].sel(depth_surface = depth_index).plot(figsize=(11, 7),cmap='inferno',vmin=2., vmax=12.)
    plt.ylabel(None); plt.xlabel(None)
    if depth_index == 0: msg = 'This is for surface water'
    else:                msg = 'This is for water at ' + str(int(glodap['T']['Depth'].values[depth_index])) + ' meters depth'
    plt.text(25, -87, msg); plt.text(47, 50, 'temperature of'); plt.text(47, 42, 'ocean water')
    
def nitrate(depth_index):
    glodap['N']['NO3'].sel(depth_surface = depth_index).plot(figsize=(11, 7),cmap='magma', vmin=2., vmax=40.)
    plt.ylabel(None); plt.xlabel(None)
    if depth_index == 0: msg = 'This is for surface water'
    else:                msg = 'This is for water at ' + str(int(glodap['N']['Depth'].values[depth_index])) + ' meters depth'
    plt.text(25, -87, msg); plt.text(47, 50, 'nitrate in'); plt.text(47, 42, 'ocean water')

def carbonate(depth_index):
    glodap['R']['TCO2'].sel(depth_surface = depth_index).plot(figsize=(11, 7), cmap='cividis', vmin=2000., vmax=2500.)
    plt.ylabel(None); plt.xlabel(None)
    if depth_index == 0: msg = 'This is for surface water'
    else:                msg = 'This is for water at ' + str(int(glodap['R']['Depth'].values[depth_index])) + ' meters depth'
    plt.text(25, -87, msg); plt.text(47, 50, 'carbon dioxide in'); plt.text(47, 42, 'ocean water')

interact(oxygen,      depth_index=widgets.IntSlider(min=0, max=32, step=1, value=0, continuous_update=False, description='O depth'))
interact(salinity,    depth_index=widgets.IntSlider(min=0, max=32, step=1, value=0, continuous_update=False, description='S depth'))
interact(temperature, depth_index=widgets.IntSlider(min=0, max=32, step=1, value=0, continuous_update=False, description='T depth'))
interact(nitrate,     depth_index=widgets.IntSlider(min=0, max=32, step=1, value=0, continuous_update=False, description='NO3 depth'))
interact(carbonate,   depth_index=widgets.IntSlider(min=0, max=32, step=1, value=0, continuous_update=False, description='CO2 depth'))

interactive(children=(IntSlider(value=0, continuous_update=False, description='O depth', max=32), Output()), _…

interactive(children=(IntSlider(value=0, continuous_update=False, description='S depth', max=32), Output()), _…

interactive(children=(IntSlider(value=0, continuous_update=False, description='T depth', max=32), Output()), _…

interactive(children=(IntSlider(value=0, continuous_update=False, description='NO3 depth', max=32), Output()),…

interactive(children=(IntSlider(value=0, continuous_update=False, description='CO2 depth', max=32), Output()),…

<function __main__.carbonate(depth_index)>

## Set the slider above to 28

Compare with the mid-ocean ridges shown here.


<BR>
<img src="../images/maps/lithosphere_age.png" style="float: left;" alt="drawing" width="1000"/>
<div style="clear: left"><BR>